In [1]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
sys.path.append('../../src/')
from train import load_data
# from diffusion import DiffusionModel
# from evaluate import get_results
from omegaconf import OmegaConf
# from main import load_data, make_model
import numpy as np
import os
import glob
import matplotlib.animation as animation
from matplotlib.animation import PillowWriter
import torch
from model2 import Autoencoder, Preprocessor
import magic
import torch
import pathlib
wandb.login()
api = wandb.Api()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: xingzhis. Use `wandb login --relogin` to force relogin


In [2]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
from omegaconf import OmegaConf
import os
import glob
import numpy as np
import torch
from torch import nn
import torch.optim as optim
from geodesic import jacobian, velocity, CondCurve, GeodesicBridge
from plotly3d.plot import scatter, trajectories
import torch
from torch import nn
import pytorch_lightning as pl
from procrustes import Procrustes
from torch.utils.data import DataLoader, TensorDataset

In [3]:
entity = "xingzhis"
project = "dmae"
sweep_id = 'kcrvri6d'
sweep = api.sweep(f"{entity}/{project}/{sweep_id}")
# Initialize an empty list to store run data
runs_data = []

# Iterate through each run in the sweep
for run in sweep.runs:
    # Extract metrics and configs
    metrics = run.summary._json_dict
    configs = run.config
    
    # Combine metrics and configs, and add run ID
    combined_data = {**metrics, **configs, "run_id": run.id}
    
    # Append the combined data to the list
    runs_data.append(combined_data)

# Create a DataFrame from the runs data
df = pd.DataFrame(runs_data)

In [4]:
data_name = 'hemisphere'
dist_mask = 'False'
noise_type = 'hi-freq-no-add'
noise_level = 1.0
savefolder = None
plot_x = False
run_id = df[(df['data.name'] == 'hemisphere') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy/False/') & (df['cfg/dimensions/latent'] == 2) & (df['cfg/loss/weights/negative'] == 1.)][['run_id']]
assert len(run_id) == 1
run_id = run_id['run_id'].values[0]
run = api.run(f"{entity}/{project}/{run_id}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
z = z[data['mask_x'].astype(bool)]

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning: Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.
  rank_zero_warn(


In [5]:
scatter(xh, data['mask_x'])

In [6]:
scatter(zhh, data['mask_x'])

In [8]:
# Swiss roll random integer
# np.random.seed(3450)
# np.random.seed(3451)
# np.random.seed(3452)
np.random.seed(345123)
npts = data['mask_x'].sum()
zs = []
n = 20
for i in range(n):
    start = np.random.randint(0,npts,size=1)
    # end = np.random.randint(0,npts,size=1)
    zs.append(torch.tensor(z[start,:]).cpu())
    # xends.append(torch.tensor(z[end,:]).cpu())
end = np.random.randint(0,npts,size=1)
# zfin = torch.tensor([[0,0,1]], dtype=torch.float32)
zfin = torch.tensor(z[end,:]).cpu() 
zbatch = torch.cat(zs,0)
zendbatch = torch.cat([zfin for i in range(n)],0)

print(zfin.shape)
print(zbatch.shape)
print(zendbatch.shape)

import matplotlib.pyplot as plt
fig = plt.figure()
# ax = fig.add_subplot(111, projection='3d')
scprep.plot.scatter2d(z.detach().cpu().numpy(), ax=ax)
for i in range(zbatch.shape[0]):
    scprep.plot.scatter2d(zbatch[i].detach().cpu().numpy(), ax=ax, c='g')
    # scprep.plot.scatter2d(zhat_no_len_reg[:,i,:].detach().cpu().numpy(), ax=ax)
scprep.plot.scatter2d(zfin[0].detach().cpu().numpy(), ax=ax, c='r')

with torch.no_grad():
    xbatch = model.decoder(zbatch, unnormalize=False)
    xendbatch = model.decoder(zendbatch, unnormalize=False)

dataset = TensorDataset(xbatch, xendbatch)
dataloader = DataLoader(dataset, batch_size=len(z), shuffle=True)

torch.Size([1, 2])
torch.Size([20, 2])
torch.Size([20, 2])


/tmp/tmp.MoQyFNIPnt/ipykernel_3993288/747528509.py:12: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/tmp/tmp.MoQyFNIPnt/ipykernel_3993288/747528509.py:16: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



<Figure size 640x480 with 0 Axes>

In [9]:
x.size()

torch.Size([5365, 3])

In [10]:
def func(x):
    return model.encoder(x)

gbmodel = GeodesicBridge(
    func=func,
    input_dim=x.size(1), 
    hidden_dim=32, 
    scale_factor=1, 
    symmetric=True, 
    num_layers=3, 
    n_tsteps=100, 
    lr=1e-3, 
    weight_decay=1e-5,
)
trainer = pl.Trainer(max_epochs=200)
trainer.fit(gbmodel, dataloader)
trainer.save_checkpoint("hsphere_1.0.ckpt")

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/lightning_fabric/plugins/environments/slurm.py:165: PossibleUserWarning:

The `srun` command is available on your system but is not used. HINT: If your intention is to run Lightning on SLURM, prepend your python command with `srun` like so: srun python /gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_env ...

GPU available: True (cuda), used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/trainer/setup.py:176: PossibleUserWarning:

GPU available but not used. Set `accelerator` and `devices` using `Trainer(accelerator='gpu', devices=1)`.

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/trainer/configuration_validator.py:108: PossibleUserWarning:

You defined a `validation_step` but have no `val_dataloader`. Skipping val loop.

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/callbacks/model_checkpoint.py:613: UserWarning:

Checkpoint directory /gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/dmae/notebooks/geodesic/lightning_logs/version_31320806/checkpoints exists and is not empty.


  | Name | Type      | Params
-----------------------------------
0 | cc   | CondCurve | 10.9 K
-----------------------------------
10.9 K    Trainable params
0         N

Training: 0it [00:00, ?it/s]

`Trainer.fit` stopped: `max_epochs=200` reached.


In [11]:
x0, x1 = next(iter(dataloader))

In [12]:
x0, x1 = next(iter(dataloader))
with torch.no_grad():
    xhat = gbmodel(x0, x1, gbmodel.ts)

In [13]:
import torch
xshape = xhat.shape
xflatten = xhat.flatten(0,1)
with torch.no_grad():
    zhat_flatten = model.encoder(xflatten, normalize=False)
    zhat = zhat_flatten.reshape(xshape[0], xshape[1], -1)
    z0 = model.encoder(x0, normalize=False)
    z1 = model.encoder(x1, normalize=False)

In [14]:
# data_amb = torch.concat([xflatten, z0, z1, x[data['mask_x'].astype(bool)]]).cpu().numpy()

RuntimeError: Sizes of tensors must match except in dimension 0. Expected size 3 but got size 2 for tensor number 1 in the list.

In [ ]:
# import phate
# phate_op = phate.PHATE(n_components=3, random_state=42)
# data_lat = phate_op.fit_transform(data_amb)

In [15]:
colors = np.r_[np.ones(xflatten.shape[0])*0, np.ones(z0.shape[0])*1, np.ones(z1.shape[0])*2, np.ones(x[data['mask_x'].astype(bool)].shape[0])*3]

In [16]:
# scatter(data_lat, colors, s=2)

In [18]:
fig = scatter(model.encoder.preprocessor.normalize(x).cpu().numpy(), data['mask_x'], s=2)
fig = scatter(x0.detach().cpu().numpy(), s=10, fig=fig)
fig = scatter(x1.detach().cpu().numpy(), s=10, fig=fig)
# fig = trajectories(longitudelines.detach().cpu().numpy(), s=5, c='blue', fig=fig)
fig = trajectories(xhat.detach().cpu().numpy(), s=10, fig=fig, title='Geodesic Bridge', filename='hsphere_geod_1.0_2d.html')
fig.show()

In [19]:
fig = scatter(z.cpu().numpy(), s=2)
fig = scatter(z0.detach().cpu().numpy(), s=10, fig=fig)
fig = scatter(z1.detach().cpu().numpy(), s=10, fig=fig)
# fig = trajectories(longitudelines.detach().cpu().numpy(), s=5, c='blue', fig=fig)
fig = trajectories(zhat.detach().cpu().numpy(), s=10, fig=fig, title='Geodesic Bridge', filename='hsphere_geod_1.0_latent.html')
fig.show()